In [1]:
import numpy as np
import struct
import matplotlib.pyplot as plt
import math 

train_images = './train-images.idx3-ubyte'
train_labels = './train-labels.idx1-ubyte'
test_images = './t10k-images.idx3-ubyte'
test_labels = './t10k-labels.idx1-ubyte'



def loadimages(train_images):
    print("--------------------------------------------------")
    print("Now on ",train_images)
    train_images = open(train_images, 'rb').read()
    offset = 0
    fmt_header = '>iiii'
    #Represent BIG ENDIAN   I represent INTEGER
    magic_number, num_images, num_rows, num_cols = struct.unpack_from(fmt_header, train_images, offset)
    print("Magic:%d, Number of image: %d, Image size: %d*%d"% (magic_number, num_images, num_rows, num_cols))
    image_size = num_rows * num_cols
    offset += struct.calcsize(fmt_header)
    print("offset is ",offset)

    fmt_image = '>' + str(image_size) + 'B'
    print("fmt_image is " ,fmt_image)

    images = np.empty((num_images, num_rows, num_cols))
    print("images shape is " ,images.shape)

    for i in range(num_images):
        if (i + 1) % num_images == 0:
            print('Already  %d' % (i + 1) + 'pictures')
        images[i] = np.array(struct.unpack_from(fmt_image, train_images, offset)).reshape((num_rows, num_cols))
        offset += struct.calcsize(fmt_image)
    return images

def loadlabel(train_labels):
    print("---------------------------------")
    print("Now on",train_labels)
    bin_data = open(train_labels, 'rb').read()
    offset = 0
    fmt_header = '>ii'
    magic_number, num_images = struct.unpack_from(fmt_header, bin_data, offset)
    print('Magic:%d, Number of images: %d' % (magic_number, num_images))
    offset += struct.calcsize(fmt_header)
    fmt_image = '>B'
    print("fmt_image is ",struct.calcsize(fmt_image))
    labels = np.empty(num_images)
    for i in range(num_images):
        if (i + 1) % num_images == 0:
            print('Already %d' % (i + 1) + 'pictures')
        labels[i] = struct.unpack_from(fmt_image, bin_data, offset)[0]
        offset += struct.calcsize(fmt_image)
    return labels
train_images = loadimages(train_images)
train_labels = loadlabel(train_labels)
test_images  = loadimages(test_images)
test_labels  = loadlabel(test_labels)
print("--------- prior------------")
prior=[0]*10 
num_of_label=[0]*10
for i in range(len(train_labels)):
    prior[int(train_labels[i])]+=1
    num_of_label[int(train_labels[i])]+=1
_sum=0
for i in range(len(prior)):
    prior[i]/=len(train_labels)
prior=np.array(prior)
print(prior)

#-----------------------------------------------------------------------------------------------------------

train_images = train_images.reshape(60000,784)
test_images  = test_images.reshape(10000,784) 
mean = np.zeros((10,28*28),dtype = np.float64)
std  = np.zeros((10,28*28),dtype = np.float64)
for index , label in enumerate(np.unique(train_labels)):   #np.unique sort and remove repeat numbers
    label_index = np.where(label==train_labels)
    mean[index] = np.mean(train_images[label_index],axis=0)
    std[index]  = np.std(train_images[label_index],axis =0)
print(std[0].shape)
std = std + 20
print(np.min(std))
#-----------------------------------------------------------------------------------------------------------
def continous(test_images,mean,std,test_labels):
    log_p_test = np.zeros(10, dtype = 'float64')
    count = 0
    for k in range(10000):
        log_likelihood=[0]*10
        log_likelihood=np.array(log_likelihood,dtype=float)
        for i in range(10):
            temp = 0
            log_p_test[i] = (prior[i])
            for j in range(784):
                if std[i][j]!=0:
                   
                    #log_p_test[i] += -1/2*np.log(std[i,j]*2*math.pi) -1/2*((test_images[k, j] - mean[i,j]) ** 2) / std[i,j]
                   
                
                    log_inside=float(2*(math.pi)*(std[i][j]**2))
                    log_inside=math.sqrt(log_inside)
                    first_part=float(math.log(log_inside))
                    second_part=float(((test_images[k][j]-mean[i][j])**2)/(2*(std[i][j])))
                    temp=float(temp+first_part+second_part)
                    log_p_test[i] = temp + math.log(prior[i])
                
                    #exp_term = (-1/2)*(test_images[k][j]-mean[i][j])**2/(std[i][j]**2)
                    #first_term = math.log(math.sqrt(1/(2*(math.pi)*std[i][j]**2)))
                    #temp = first_term + exp_term +temp
            temp = temp + math.log(prior[i])
            temp = temp
            log_likelihood[i]=temp  
        predict = (np.argmin(log_likelihood))
        result = test_labels[k]
        normalize_sum=0
        
        for i in range(10):
            normalize_sum+=log_likelihood[i]
        for i in range(10):
            log_likelihood[i]=float(log_likelihood[i]/normalize_sum)
        
        print("-----------------------")
        print("image[%d]"%k)
        for i in range(len(log_likelihood)):
            print('%d   %f'%(i,log_likelihood[i]))
        
        
        print("predict is",(np.argmin(log_likelihood)))
        print("Result is %d"%test_labels[k])
        if predict == result :
            count =count+1
        #break
    accuracy = float(count/10000)
    error    = 1-accuracy
    print("Accuracy is %f"%accuracy)
    print("Error is %f"%error)
    
 
#-----------------------------------------------------------------------------------------------------------
def discrete(test_images,mean,std,test_labels,train_labels,train_images,num_of_label,prior):
    count = 0
    print("Start to calculate training data")
    train_discrete_images=np.zeros((10,784,32),dtype=np.float64)
    for i in range(60000):
        label_num=int(train_labels[i])
        for j in range(784):
            class_of_pixel=int(train_images[i][j]/8)
            train_discrete_images[label_num][j][class_of_pixel]+=1
    
    for i in range(10):
        train_discrete_images[i]=train_discrete_images[i]/int(num_of_label[i])
    print("-----------------Here-------------------------")
    print(train_discrete_images[:, 0, 0:16])
    print("-----------------Here-------------------------")
    print("Start to calculate testing data")
    
    for im in range(10000):
        likelihood=[0]*10
        likelihood=np.array(likelihood,dtype=np.float64)
        for i in range(10):
            temp=0
            for j in range(784):
                now_bin=int(test_images[im][j]/8)
                temp+=np.log(train_discrete_images[i][j][now_bin]) +0.001
                #print("The iteration is %d %.70f"%(j,temp))
            temp+=np.log(prior[i])
            likelihood[i]=temp        
        #for i in range(len(likelihood)):
        #    print("%.50f"%likelihood[i])
        predict = (np.argmax(likelihood))
        result = test_labels[im]  
        normalize_sum=0  
        for i in range(10):
            normalize_sum+=likelihood[i]
        for i in range(10):
            likelihood[i]=float(likelihood[i]/normalize_sum)
        
                  
        
        print("-----------------------")
        print("image[%d]"%im)
        for i in range(len(likelihood)):
            print('%d   %f'%(i,likelihood[i]))
        
        
        print("predict is %d"%predict)
        print("Result is %d"%test_labels[im])
        if predict == result :
            count =count+1
        #break
    accuracy = float(count/10000)
    error    = 1-accuracy
    print("Accuracy is %f"%accuracy)
    print("Error is %f"%error)
    
    print("Imagination of numbers in Bayssian classifier:")
    for label in range(10):
        print("%d :"%(label))
        matrix = [0]*784
        for pixel in range(784):
            mean = 0
            for bin in range(32):
                mean += train_discrete_images[label][pixel][bin]*bin
            if pixel%28 == 0:
                print("")
            if mean <=15:
                print("0",end="")
            else:
                print("1",end="")
        #print("")
    """
    imagination = np.zeros((10, 784), dtype = 'int')

    for i in range(784):
        imagination[:, i] = np.sum(train_discrete_images[:, i, 0:16], axis = 1) < 1/2
    # print the imagination
    for i in range(10):
        print(str(i) + ':')
        for j in range(1, 784+1):
            print(imagination[i, j-1], sep = ' ', end = '')
            if j % 28 == 0:
                print()
    """



--------------------------------------------------
Now on  ./train-images.idx3-ubyte
Magic:2051, Number of image: 60000, Image size: 28*28
offset is  16
fmt_image is  >784B
images shape is  (60000, 28, 28)
Already  60000pictures
---------------------------------
Now on ./train-labels.idx1-ubyte
Magic:2049, Number of images: 60000
fmt_image is  1
Already 60000pictures
--------------------------------------------------
Now on  ./t10k-images.idx3-ubyte
Magic:2051, Number of image: 10000, Image size: 28*28
offset is  16
fmt_image is  >784B
images shape is  (10000, 28, 28)
Already  10000pictures
---------------------------------
Now on ./t10k-labels.idx1-ubyte
Magic:2049, Number of images: 10000
fmt_image is  1
Already 10000pictures
--------- prior------------
[0.09871667 0.11236667 0.0993     0.10218333 0.09736667 0.09035
 0.09863333 0.10441667 0.09751667 0.09915   ]
(784,)
20.0


In [2]:
continous(test_images,mean,std,test_labels) 

-----------------------
image[0]
0   0.120085
1   0.163705
2   0.110599
3   0.093124
4   0.082656
5   0.086012
6   0.143175
7   0.040847
8   0.093743
9   0.066053
predict is 7
Result is 7
-----------------------
image[1]
0   0.089129
1   0.125015
2   0.057317
3   0.074262
4   0.117054
5   0.078084
6   0.073549
7   0.160498
8   0.087648
9   0.137444
predict is 2
Result is 2
-----------------------
image[2]
0   0.157459
1   0.041244
2   0.091287
3   0.099049
4   0.104992
5   0.088227
6   0.105401
7   0.109870
8   0.095579
9   0.106890
predict is 1
Result is 1
-----------------------
image[3]
0   0.044014
1   0.238874
2   0.084465
3   0.089157
4   0.098603
5   0.076269
6   0.070516
7   0.111299
8   0.085837
9   0.100966
predict is 0
Result is 0
-----------------------
image[4]
0   0.103433
1   0.212658
2   0.086442
3   0.105919
4   0.058976
5   0.086148
6   0.095413
7   0.086182
8   0.091919
9   0.072909
predict is 4
Result is 4
-----------------------
image[5]
0   0.169689
1   0.039116
2

-----------------------
image[49]
0   0.105638
1   0.228257
2   0.079993
3   0.099207
4   0.055389
5   0.088975
6   0.091450
7   0.084843
8   0.090187
9   0.076061
predict is 4
Result is 4
-----------------------
image[50]
0   0.103250
1   0.157172
2   0.083307
3   0.086090
4   0.098169
5   0.074072
6   0.055119
7   0.140834
8   0.089793
9   0.112194
predict is 6
Result is 6
-----------------------
image[51]
0   0.091711
1   0.207478
2   0.077698
3   0.060052
4   0.094128
5   0.076846
6   0.089379
7   0.109108
8   0.086387
9   0.107213
predict is 3
Result is 3
-----------------------
image[52]
0   0.094913
1   0.173303
2   0.110820
3   0.092463
4   0.078358
5   0.060114
6   0.118463
7   0.101480
8   0.083387
9   0.086699
predict is 5
Result is 5
-----------------------
image[53]
0   0.093298
1   0.169852
2   0.094061
3   0.073327
4   0.090565
5   0.068877
6   0.098239
7   0.117710
8   0.089627
9   0.104445
predict is 5
Result is 5
-----------------------
image[54]
0   0.082288
1   0.18

-----------------------
image[98]
0   0.079036
1   0.159735
2   0.073598
3   0.098000
4   0.096060
5   0.074374
6   0.057915
7   0.149246
8   0.089144
9   0.122891
predict is 6
Result is 6
-----------------------
image[99]
0   0.124134
1   0.222993
2   0.090672
3   0.098058
4   0.060755
5   0.087583
6   0.104350
7   0.077293
8   0.081314
9   0.052848
predict is 9
Result is 9
-----------------------
image[100]
0   0.107478
1   0.153811
2   0.076447
3   0.101280
4   0.085507
5   0.094148
6   0.063752
7   0.113442
8   0.097792
9   0.106343
predict is 6
Result is 6
-----------------------
image[101]
0   0.045484
1   0.206885
2   0.091089
3   0.091842
4   0.094635
5   0.068779
6   0.102772
7   0.117673
8   0.081645
9   0.099194
predict is 0
Result is 0
-----------------------
image[102]
0   0.096494
1   0.183127
2   0.120727
3   0.082847
4   0.082420
5   0.058276
6   0.147762
7   0.078423
8   0.071889
9   0.078035
predict is 5
Result is 5
-----------------------
image[103]
0   0.093898
1   

predict is 0
Result is 0
-----------------------
image[149]
0   0.124270
1   0.135837
2   0.081540
3   0.095891
4   0.087650
5   0.081591
6   0.090792
7   0.118890
8   0.093612
9   0.089927
predict is 2
Result is 2
-----------------------
image[150]
0   0.124306
1   0.209274
2   0.095309
3   0.092761
4   0.062615
5   0.080196
6   0.099915
7   0.097315
8   0.080163
9   0.058146
predict is 9
Result is 9
-----------------------
image[151]
0   0.106066
1   0.186486
2   0.079272
3   0.083358
4   0.076085
5   0.082493
6   0.123251
7   0.103227
8   0.080147
9   0.079615
predict is 4
Result is 9
-----------------------
image[152]
0   0.101159
1   0.143199
2   0.108563
3   0.110666
4   0.081449
5   0.062677
6   0.127622
7   0.098327
8   0.077447
9   0.088890
predict is 5
Result is 5
-----------------------
image[153]
0   0.098399
1   0.151952
2   0.095425
3   0.069540
4   0.109664
5   0.063002
6   0.107470
7   0.123698
8   0.077991
9   0.102858
predict is 5
Result is 5
-----------------------
i

-----------------------
image[197]
0   0.117025
1   0.136464
2   0.078181
3   0.102705
4   0.093003
5   0.078078
6   0.052600
7   0.152851
8   0.075735
9   0.113358
predict is 6
Result is 6
-----------------------
image[198]
0   0.147496
1   0.173205
2   0.108029
3   0.096191
4   0.058570
5   0.078750
6   0.118859
7   0.079339
8   0.080043
9   0.059518
predict is 4
Result is 4
-----------------------
image[199]
0   0.108673
1   0.141032
2   0.049002
3   0.078491
4   0.116278
5   0.087110
6   0.100885
7   0.137004
8   0.060860
9   0.120663
predict is 2
Result is 2
-----------------------
image[200]
0   0.077874
1   0.188798
2   0.059776
3   0.053913
4   0.108869
5   0.069756
6   0.087993
7   0.155271
8   0.070214
9   0.127535
predict is 3
Result is 3
-----------------------
image[201]
0   0.066419
1   0.209455
2   0.066906
3   0.104738
4   0.083836
5   0.091899
6   0.053352
7   0.115905
8   0.096121
9   0.111368
predict is 6
Result is 6
-----------------------
image[202]
0   0.161631
1 

...

-----------------------
image[9778]
0   0.072850
1   0.192480
2   0.063835
3   0.083066
4   0.092008
5   0.075886
6   0.049503
7   0.161408
8   0.083508
9   0.125456
predict is 6
Result is 6
-----------------------
image[9779]
0   0.054122
1   0.196832
2   0.080610
3   0.096283
4   0.096996
5   0.068039
6   0.097216
7   0.123873
8   0.074435
9   0.111594
predict is 0
Result is 2
-----------------------
image[9780]
0   0.120763
1   0.114154
2   0.081046
3   0.098779
4   0.102167
5   0.083660
6   0.118458
7   0.106078
8   0.071514
9   0.103381
predict is 8
Result is 8
-----------------------
image[9781]
0   0.104465
1   0.153020
2   0.101789
3   0.106056
4   0.089071
5   0.082899
6   0.125611
7   0.069397
8   0.084380
9   0.083313
predict is 7
Result is 7
-----------------------
image[9782]
0   0.086118
1   0.159374
2   0.080187
3   0.111952
4   0.084661
5   0.069407
6   0.069900
7   0.135196
8   0.088092
9   0.115113
predict is 5
Result is 6
-----------------------
image[9783]
0   0.122

-----------------------
image[9823]
0   0.144705
1   0.121639
2   0.109387
3   0.097789
4   0.093439
5   0.087954
6   0.141645
7   0.048669
8   0.090333
9   0.064440
predict is 7
Result is 7
-----------------------
image[9824]
0   0.143106
1   0.094099
2   0.096550
3   0.086437
4   0.105754
5   0.076781
6   0.123387
7   0.126730
8   0.052742
9   0.094413
predict is 8
Result is 8
-----------------------
image[9825]
0   0.142366
1   0.164783
2   0.119843
3   0.096954
4   0.073638
5   0.078698
6   0.114212
7   0.069718
8   0.086021
9   0.053768
predict is 9
Result is 9
-----------------------
image[9826]
0   0.079570
1   0.162368
2   0.083801
3   0.094121
4   0.099373
5   0.071730
6   0.084066
7   0.139096
8   0.073692
9   0.112182
predict is 5
Result is 0
-----------------------
image[9827]
0   0.153053
1   0.091101
2   0.101751
3   0.086513
4   0.102767
5   0.076816
6   0.118537
7   0.114822
8   0.065522
9   0.089118
predict is 8
Result is 8
-----------------------
image[9828]
0   0.085

-----------------------
image[9872]
0   0.076949
1   0.150458
2   0.077746
3   0.047033
4   0.128900
5   0.064144
6   0.098904
7   0.139508
8   0.079632
9   0.136726
predict is 3
Result is 3
-----------------------
image[9873]
0   0.079236
1   0.205068
2   0.076416
3   0.113525
4   0.067056
5   0.074425
6   0.080997
7   0.115269
8   0.085278
9   0.102730
predict is 4
Result is 4
-----------------------
image[9874]
0   0.128652
1   0.098568
2   0.086058
3   0.075924
4   0.105049
5   0.081248
6   0.146403
7   0.108858
8   0.064705
9   0.104535
predict is 8
Result is 2
-----------------------
image[9875]
0   0.138704
1   0.134723
2   0.108152
3   0.100636
4   0.082060
5   0.074245
6   0.108126
7   0.103899
8   0.072456
9   0.076999
predict is 8
Result is 8
-----------------------
image[9876]
0   0.159303
1   0.058561
2   0.076335
3   0.095744
4   0.097541
5   0.090754
6   0.129676
7   0.114949
8   0.071082
9   0.106056
predict is 1
Result is 1
-----------------------
image[9877]
0   0.106

-----------------------
image[9920]
0   0.123152
1   0.107622
2   0.097190
3   0.085626
4   0.105590
5   0.077901
6   0.145840
7   0.112937
8   0.054140
9   0.090001
predict is 8
Result is 8
-----------------------
image[9921]
0   0.083785
1   0.185521
2   0.065279
3   0.095781
4   0.095632
5   0.077927
6   0.053757
7   0.142685
8   0.085453
9   0.114180
predict is 6
Result is 6
-----------------------
image[9922]
0   0.152898
1   0.108475
2   0.103465
3   0.099048
4   0.076529
5   0.077766
6   0.122583
7   0.095851
8   0.077391
9   0.085994
predict is 4
Result is 4
-----------------------
image[9923]
0   0.150017
1   0.054567
2   0.072812
3   0.095827
4   0.101654
5   0.086350
6   0.119043
7   0.125351
8   0.074901
9   0.119478
predict is 1
Result is 1
-----------------------
image[9924]
0   0.088234
1   0.195816
2   0.102166
3   0.112138
4   0.069754
5   0.080229
6   0.112911
7   0.076420
8   0.089762
9   0.072569
predict is 4
Result is 9
-----------------------
image[9925]
0   0.115

-----------------------
image[9968]
0   0.126969
1   0.139094
2   0.107599
3   0.103517
4   0.085745
5   0.086337
6   0.148739
7   0.045860
8   0.088526
9   0.067615
predict is 7
Result is 7
-----------------------
image[9969]
0   0.157730
1   0.050689
2   0.081864
3   0.096217
4   0.099582
5   0.088278
6   0.128119
7   0.111016
8   0.079152
9   0.107354
predict is 1
Result is 1
-----------------------
image[9970]
0   0.093292
1   0.132587
2   0.068734
3   0.071040
4   0.117510
5   0.071185
6   0.078388
7   0.143540
8   0.091649
9   0.132075
predict is 2
Result is 5
-----------------------
image[9971]
0   0.083335
1   0.172523
2   0.057481
3   0.095646
4   0.097481
5   0.081732
6   0.097398
7   0.118801
8   0.081599
9   0.114004
predict is 2
Result is 2
-----------------------
image[9972]
0   0.126882
1   0.178995
2   0.095810
3   0.113318
4   0.051530
5   0.084558
6   0.097446
7   0.093962
8   0.088795
9   0.068705
predict is 4
Result is 4
-----------------------
image[9973]
0   0.105

In [3]:
discrete(test_images,mean,std,test_labels,train_labels,train_images,num_of_label,prior)

Start to calculate training data
-----------------Here-------------------------
[[1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
 [1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
 [1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
 [1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
 [1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
 [1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
 [1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
 [1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
 [1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
 [1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]]
-----------------Here-------------------------
Start to calculate testing data
-----------------------
image[0]
0   nan
1   nan
2   nan
3   nan
4   nan
5   nan
6   nan
7   0.000000
8   nan
9   0.000000
predict is 7
Result is 7
-----------------------
image[1]
0   nan
1   nan
2   nan
3   nan
4   nan
5   nan
6   nan
7   nan
8   nan
9   nan
predict is 0
Result is 2
-----------------------
image[2]
0   0.00000

C:\Users\USER\anaconda3\lib\site-packages\ipykernel_launcher.py:166: RuntimeWarning: divide by zero encountered in log
C:\Users\USER\anaconda3\lib\site-packages\ipykernel_launcher.py:178: RuntimeWarning: invalid value encountered in double_scalars


-----------------------
image[8]
0   nan
1   nan
2   nan
3   nan
4   0.000000
5   0.000000
6   nan
7   nan
8   nan
9   nan
predict is 4
Result is 5
-----------------------
image[9]
0   nan
1   nan
2   nan
3   nan
4   nan
5   nan
6   nan
7   0.000000
8   nan
9   0.000000
predict is 9
Result is 9
-----------------------
image[10]
0   0.000000
1   nan
2   0.000000
3   0.000000
4   0.000000
5   0.000000
6   nan
7   nan
8   0.000000
9   nan
predict is 0
Result is 0
-----------------------
image[11]
0   nan
1   nan
2   0.000000
3   0.000000
4   nan
5   nan
6   0.000000
7   nan
8   nan
9   nan
predict is 6
Result is 6
-----------------------
image[12]
0   nan
1   nan
2   nan
3   nan
4   nan
5   nan
6   nan
7   0.000000
8   nan
9   0.000000
predict is 9
Result is 9
-----------------------
image[13]
0   0.000000
1   nan
2   nan
3   0.000000
4   0.000000
5   0.000000
6   nan
7   nan
8   0.000000
9   0.000000
predict is 0
Result is 0
-----------------------
image[14]
0   0.000000
1   0.000000
2  

-----------------------
image[68]
0   0.000000
1   nan
2   0.000000
3   0.000000
4   0.000000
5   0.000000
6   nan
7   nan
8   0.000000
9   nan
predict is 3
Result is 3
-----------------------
image[69]
0   0.000000
1   nan
2   0.000000
3   nan
4   nan
5   0.000000
6   nan
7   nan
8   nan
9   nan
predict is 0
Result is 0
-----------------------
image[70]
0   nan
1   nan
2   nan
3   nan
4   nan
5   nan
6   nan
7   0.000000
8   nan
9   nan
predict is 7
Result is 7
-----------------------
image[71]
0   0.000000
1   nan
2   0.000000
3   nan
4   nan
5   0.000000
6   nan
7   nan
8   0.000000
9   nan
predict is 0
Result is 0
-----------------------
image[72]
0   0.000000
1   nan
2   0.000000
3   0.000000
4   0.000000
5   0.000000
6   nan
7   nan
8   0.000000
9   nan
predict is 2
Result is 2
-----------------------
image[73]
0   nan
1   nan
2   nan
3   nan
4   nan
5   0.000000
6   nan
7   0.000000
8   nan
9   0.000000
predict is 7
Result is 9
-----------------------
image[74]
0   0.000000
1   

4   0.000000
5   0.000000
6   nan
7   0.000000
8   0.000000
9   0.000000
predict is 2
Result is 2
-----------------------
image[120]
0   0.000000
1   nan
2   0.000000
3   0.000000
4   nan
5   0.000000
6   nan
7   nan
8   0.000000
9   nan
predict is 3
Result is 5
-----------------------
image[121]
0   0.000000
1   nan
2   0.000000
3   0.000000
4   0.000000
5   0.000000
6   0.000000
7   nan
8   0.000000
9   nan
predict is 4
Result is 4
-----------------------
image[122]
0   nan
1   nan
2   nan
3   0.000000
4   0.000000
5   0.000000
6   nan
7   0.000000
8   nan
9   0.000000
predict is 7
Result is 7
-----------------------
image[123]
0   nan
1   nan
2   0.000000
3   nan
4   nan
5   nan
6   0.000000
7   nan
8   nan
9   nan
predict is 6
Result is 6
-----------------------
image[124]
0   nan
1   nan
2   nan
3   nan
4   nan
5   nan
6   nan
7   0.000000
8   nan
9   nan
predict is 7
Result is 7
-----------------------
image[125]
0   nan
1   nan
2   nan
3   nan
4   0.000000
5   0.000000
6   nan
7

...

-----------------------
image[9811]
0   0.000000
1   0.000000
2   0.000000
3   0.000000
4   0.000000
5   0.000000
6   nan
7   nan
8   0.000000
9   nan
predict is 8
Result is 2
-----------------------
image[9812]
0   0.000000
1   nan
2   0.000000
3   0.000000
4   nan
5   0.000000
6   nan
7   nan
8   0.000000
9   nan
predict is 3
Result is 3
-----------------------
image[9813]
0   0.000000
1   nan
2   0.000000
3   0.000000
4   0.000000
5   0.000000
6   nan
7   nan
8   0.000000
9   nan
predict is 4
Result is 4
-----------------------
image[9814]
0   nan
1   nan
2   nan
3   nan
4   0.000000
5   0.000000
6   nan
7   nan
8   0.000000
9   nan
predict is 5
Result is 5
-----------------------
image[9815]
0   0.000000
1   nan
2   0.000000
3   nan
4   nan
5   0.000000
6   0.000000
7   nan
8   nan
9   nan
predict is 6
Result is 6
-----------------------
image[9816]
0   nan
1   nan
2   nan
3   nan
4   nan
5   nan
6   nan
7   0.000000
8   nan
9   0.000000
predict is 7
Result is 7
-------------------

-----------------------
image[9866]
0   nan
1   nan
2   nan
3   nan
4   0.000000
5   0.000000
6   nan
7   nan
8   nan
9   nan
predict is 4
Result is 4
-----------------------
image[9867]
0   0.000000
1   nan
2   0.000000
3   0.000000
4   0.000000
5   0.000000
6   nan
7   nan
8   0.000000
9   nan
predict is 8
Result is 2
-----------------------
image[9868]
0   nan
1   nan
2   nan
3   nan
4   nan
5   nan
6   nan
7   0.000000
8   nan
9   0.000000
predict is 7
Result is 7
-----------------------
image[9869]
0   nan
1   nan
2   nan
3   nan
4   nan
5   nan
6   nan
7   0.000000
8   nan
9   0.000000
predict is 7
Result is 7
-----------------------
image[9870]
0   0.000000
1   nan
2   0.000000
3   0.000000
4   0.000000
5   0.000000
6   nan
7   nan
8   0.000000
9   nan
predict is 5
Result is 5
-----------------------
image[9871]
0   0.000000
1   nan
2   0.000000
3   0.000000
4   0.000000
5   0.000000
6   0.000000
7   nan
8   0.000000
9   nan
predict is 4
Result is 4
-----------------------
image

-----------------------
image[9919]
0   nan
1   nan
2   nan
3   nan
4   nan
5   nan
6   nan
7   0.000000
8   nan
9   0.000000
predict is 7
Result is 7
-----------------------
image[9920]
0   0.000000
1   0.000000
2   0.000000
3   0.000000
4   0.000000
5   0.000000
6   nan
7   0.000000
8   0.000000
9   0.000000
predict is 8
Result is 8
-----------------------
image[9921]
0   nan
1   nan
2   nan
3   nan
4   nan
5   nan
6   0.000000
7   nan
8   nan
9   nan
predict is 6
Result is 6
-----------------------
image[9922]
0   0.000000
1   nan
2   0.000000
3   0.000000
4   0.000000
5   0.000000
6   nan
7   nan
8   0.000000
9   nan
predict is 4
Result is 4
-----------------------
image[9923]
0   0.000000
1   0.000000
2   0.000000
3   0.000000
4   0.000000
5   0.000000
6   nan
7   nan
8   0.000000
9   nan
predict is 1
Result is 1
-----------------------
image[9924]
0   nan
1   nan
2   nan
3   nan
4   nan
5   nan
6   nan
7   nan
8   nan
9   nan
predict is 0
Result is 9
-----------------------
image

-----------------------
image[9974]
0   0.000000
1   nan
2   0.000000
3   0.000000
4   0.000000
5   0.000000
6   0.000000
7   nan
8   0.000000
9   nan
predict is 4
Result is 4
-----------------------
image[9975]
0   0.000000
1   nan
2   0.000000
3   0.000000
4   nan
5   0.000000
6   nan
7   nan
8   0.000000
9   nan
predict is 2
Result is 3
-----------------------
image[9976]
0   0.000000
1   nan
2   0.000000
3   0.000000
4   0.000000
5   0.000000
6   0.000000
7   nan
8   0.000000
9   nan
predict is 6
Result is 6
-----------------------
image[9977]
0   0.000000
1   nan
2   0.000000
3   0.000000
4   0.000000
5   0.000000
6   nan
7   nan
8   0.000000
9   nan
predict is 4
Result is 4
-----------------------
image[9978]
0   0.000000
1   0.000000
2   nan
3   0.000000
4   nan
5   0.000000
6   nan
7   nan
8   0.000000
9   nan
predict is 1
Result is 1
-----------------------
image[9979]
0   nan
1   nan
2   nan
3   nan
4   nan
5   nan
6   nan
7   0.000000
8   nan
9   0.000000
predict is 7
Result

0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
0000000001111111111100000000
0000000011111111111100000000
0000000001111000111100000000
0000000000000000011100000000
0000000000000000011100000000
0000000000000000111000000000
0000000000000000111000000000
0000000000000001111000000000
0000000000000001110000000000
0000000000000011110000000000
0000000000000011100000000000
0000000000000011000000000000
0000000000000111000000000000
0000000000000110000000000000
0000000000000100000000000000
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
00000000000000000000000000008 :

0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
0000000000000001110000000000
0000000000001111111100000000
0000000000011111111100000000
0000000000